# Ablaition Study

In [1]:
import pandas as pd 
import numpy as np 
from foodrec.config.structure.dataset_enum import ModelEnum 
from foodrec.evaluation.create_dataset import create_dataset
from foodrec.evaluation.is_ketogen import is_ketogenic, calc_keto_ratio
from foodrec.config.structure.paths import CONVERSATION, DATASET_PATHS
import json
from foodrec.evaluation.metrics.metrics import macro_over_queries,filter_search, micro_over_queries, accuracy,plot_pr_curves, f1_score, mean_average_precision_over_queries, mean_pr_auc_over_queries, bias_conformity_rate_at_k
from foodrec.data.all_recipe import AllRecipeLoader
from typing import Dict, List, Any, Tuple
from collections import Counter
from foodrec.agents.agent_names import AgentEnum
from foodrec.tools.ingredient_normalizer import IngredientNormalisation
from foodrec.evaluation.is_ketogen import calc_keto_ratio
from analysis_helper.load_dataset import check_availability
from foodrec.config.structure.dataset_enum import DatasetEnum
from foodrec.evaluation.reward_evaluation import final_episode_reward, routing_accuracy
from datetime import datetime
import math
from analysis_helper.load_dataset import get_dicts_set, get_search_engine
from analysis_helper.get_lowes_highest import take_25_lowest_keto
from analysis_helper.get_metrics import calc_metrics
from analysis_helper.mean_rounds import calc_rounds
from analysis_helper.query_analysis import calc_other_recommendation_parameters
from analysis_helper.calc_routing_reward import get_reward_set, reward_average_calculation
from analysis_helper.calc_path_length import calc_path_length
from analysis_helper.most_common_path import most_common_path
from analysis_helper.time import calc_mean_time
from analysis_helper.token_calculation import calc_openai_costs, calc_gemini_costs
from analysis_helper.reflector_analysis import cals_reflector_accuracy
from analysis_helper.ketogen_available import ketogen_available

In [13]:
query_set = pd.read_csv(DATASET_PATHS / "zw_personas.csv")
model = ModelEnum.Gemini

In [14]:
def get_paths(model_name):
    return {
        "PATH_NO_BIASE": CONVERSATION / model_name / "no_biase",
        "PATH_SYSTEM_BIASE": CONVERSATION / model_name / "system_biase",
        "PATH_SEARCH_ENGINE": CONVERSATION / ModelEnum.Gemini.name / "search_engine" / "res_one.json",
        "PATH_SEARCH_BIASE": CONVERSATION / model_name / "search_biase" ,
        "PATH_BOTH": CONVERSATION / model_name / "both_biase"
    }

In [15]:
paths = get_paths(ModelEnum.Gemini.name)

## Ursachen Analyse fuer die Ergebnisse der Hypothesen

### task success rate aus unteren 25 oberen 25

In [16]:
q_set_highest = take_25_lowest_keto(query_set,paths, ModelEnum.Gemini, high=True)
pr_auc_raw_high = calc_metrics(query_set=q_set_highest, paths=paths, model_name=ModelEnum.Gemini, ref_include=False)

25%: 0.2624075915346725
75%: 0.4752273733006868
Mean: 0.4078187139691796
Max: 1.565975754772325
28
2.1010442773600673 25 9.357142857142858 25
21.5 25 19.09621212121212 25
10.342857142857138 100 55.0 100
24.0 25 13.66678845451224 25
25.0 25 9.521862948077782 25
               Macro Precision  Macro Recall  Macro F1  Micro Precision  \
Bias                                                                      
No Biase              0.084042      0.374286  0.137263         0.105590   
System Biase          0.860000      0.763848  0.809078         0.982143   
Search Engine         0.103429      0.550000  0.174115         0.104569   
Search Biase          0.960000      0.546672  0.696641         1.000000   
Both Biase            1.000000      0.380875  0.551642         1.000000   

               Micro Recall  Micro F1  Mean Average Precision  Mean PR-AUC  \
Bias                                                                         
No Biase           0.414634  0.168317                0.20

In [17]:
q_set_low = take_25_lowest_keto(query_set,paths, ModelEnum.Gemini, high=False)
pr_auc_raw_low = calc_metrics(query_set=q_set_low, paths=paths, model_name=ModelEnum.Gemini, ref_include=False)

25%: 0.2624075915346725
75%: 0.4752273733006868
Mean: 0.4078187139691796
Max: 1.565975754772325
34
1.4023809523809525 25 6.5 25
13.666666666666668 25 14.833333333333334 25
10.342857142857138 100 55.0 100
21.617424242424242 25 12.972010929179714 25
23.5 25 7.266743480014867 25
               Macro Precision  Macro Recall  Macro F1  Micro Precision  \
Bias                                                                      
No Biase              0.056095      0.260000  0.092281         0.081301   
System Biase          0.546667      0.593333  0.569045         0.675000   
Search Engine         0.103429      0.550000  0.174115         0.104569   
Search Biase          0.864697      0.518880  0.648571         0.930070   
Both Biase            0.940000      0.290670  0.444034         0.988095   

               Micro Recall  Micro F1  Mean Average Precision  Mean PR-AUC  \
Bias                                                                         
No Biase           0.500000  0.139860    

### Reflector Ablehnung warum

### - wie veraendert sich die accuracy wenn man nicht verbessern darf

In [18]:
def calc_no_improvment(df, paths, model_name: ModelEnum):
    def calc_median_rounds(df, model:ModelEnum, Path):
        ls = []
        for index, row in df.iterrows():
            persona_id = row["id"]
            query = row["query"]
            ls.append(cals_reflector_accuracy(persona_id=persona_id, query=query, model=model, Path=Path))
        return ls
    ls_no_biase = calc_median_rounds(df, model_name, paths['PATH_NO_BIASE'])
    ls_system_biase = calc_median_rounds(df, model_name, paths['PATH_SYSTEM_BIASE'])
    ls_search_biase = calc_median_rounds(df, model_name, paths['PATH_SEARCH_BIASE'])
    ls_both_biase = calc_median_rounds(df, model_name, paths['PATH_BOTH'])

    print(f"Mean Rounds No Biase: Accuracy:{np.mean([True if keto > 0.8 else False for keto in ls_no_biase])}  Mean Rate {np.mean(ls_no_biase)}")
    print(f"Mean Rounds System Biase:  Accuracy:{np.mean([True if keto > 0.8 else False for keto in ls_system_biase])}  Mean Rate {np.mean(ls_system_biase)}")
    print(f"Mean Search Biase:  Accuracy:{np.mean([True if keto > 0.8 else False for keto in ls_search_biase])}  Mean Rate {np.mean(ls_search_biase)}")
    print(f"Mean Both Biase:  Accuracy:{np.mean([True if keto > 0.8 else False for keto in ls_both_biase])}  Mean Rate {np.mean(ls_both_biase)}")

In [19]:
calc_no_improvment(query_set, paths, ModelEnum.Gemini)

Mean Rounds No Biase: Accuracy:0.11  Mean Rate 0.41720981764709003
Mean Rounds System Biase:  Accuracy:0.63  Mean Rate 0.9009933569286928
Mean Search Biase:  Accuracy:0.94  Mean Rate 1.2604315432172488
Mean Both Biase:  Accuracy:0.98  Mean Rate 1.7588926057664371


### Wenn nicht ketogen war das zur auswahl

In [20]:
def was_ketogen_available(df, paths, model_name: ModelEnum):
    def calc_median_rounds(df, model:ModelEnum, Path):
        ls = []
        for index, row in df.iterrows():
            persona_id = row["id"]
            query = row["query"]
            ls.append(ketogen_available(persona_id=persona_id, query=query, model=model, Path=Path))
        filtered = [x for x in ls if x is not None]
        return filtered
    ls_no_biase = calc_median_rounds(df, model_name, paths['PATH_NO_BIASE'])
    ls_system_biase = calc_median_rounds(df, model_name, paths['PATH_SYSTEM_BIASE'])

    print(f"Mean Rounds No Biase: Accuracy: {np.mean(ls_no_biase)}")
    print(f"Mean Rounds System Biase: {np.mean(ls_system_biase)}")

In [21]:
was_ketogen_available(query_set, paths, ModelEnum.Gemini)

Mean Rounds No Biase: Accuracy: 0.6179775280898876
Mean Rounds System Biase: 0.23076923076923078


## Vergleiche Referenzmodell mit Alternative OpenAI

### Recommendations Accuracy

In [25]:
def recommendation_accuracy(df, model_name:ModelEnum):
    paths = get_paths(str(model_name.name))    
    print(10*"-"+"PATH_NO_BIASE"+10*"-")
    calc_other_recommendation_parameters(df, paths["PATH_NO_BIASE"],model_name )
    print(10*"-"+"PATH_SYSTEM_BIASE"+10*"-")
    calc_other_recommendation_parameters(df, paths["PATH_SYSTEM_BIASE"],model_name )
    print(10*"-"+"PATH_BOTH"+10*"-")
    calc_other_recommendation_parameters(df, paths["PATH_BOTH"], model_name )
    print(10*"-"+"PATH_SEARCH_BIASE"+10*"-")
    calc_other_recommendation_parameters(df, paths["PATH_SEARCH_BIASE"], model_name )

In [12]:
recommendation_accuracy(query_set, ModelEnum.OpenAI)

2025-09-14 13:49:18,244 - foodrec.data.load_ingredient_embeddings - INFO - EmbeddingLoader initialized with path: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 13:49:18,244 - foodrec.data.load_ingredient_embeddings - INFO - Starting embedding retrieval process...
2025-09-14 13:49:18,245 - foodrec.data.load_ingredient_embeddings - INFO - ✓ Found existing embeddings file: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 13:49:18,245 - foodrec.data.load_ingredient_embeddings - INFO - Loading existing embeddings...


----------PATH_NO_BIASE----------
####################Load Embeddings####################


2025-09-14 13:49:22,244 - foodrec.data.load_ingredient_embeddings - INFO - EmbeddingLoader initialized with path: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 13:49:22,245 - foodrec.data.load_ingredient_embeddings - INFO - Starting embedding retrieval process...
2025-09-14 13:49:22,245 - foodrec.data.load_ingredient_embeddings - INFO - ✓ Found existing embeddings file: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 13:49:22,245 - foodrec.data.load_ingredient_embeddings - INFO - Loading existing embeddings...


Like 0.574468085106383
 Avoid 0.9905660377358491
Cuisine 0.8928571428571429
Overall0.8192970885664583
----------PATH_SYSTEM_BIASE----------
####################Load Embeddings####################


2025-09-14 13:49:23,896 - foodrec.data.load_ingredient_embeddings - INFO - EmbeddingLoader initialized with path: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 13:49:23,897 - foodrec.data.load_ingredient_embeddings - INFO - Starting embedding retrieval process...
2025-09-14 13:49:23,897 - foodrec.data.load_ingredient_embeddings - INFO - ✓ Found existing embeddings file: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 13:49:23,897 - foodrec.data.load_ingredient_embeddings - INFO - Loading existing embeddings...


Like 0.4857142857142857
 Avoid 1.0
Cuisine 0.9
Overall0.7952380952380952
----------PATH_BOTH----------
####################Load Embeddings####################


2025-09-14 13:49:25,504 - foodrec.data.load_ingredient_embeddings - INFO - EmbeddingLoader initialized with path: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 13:49:25,505 - foodrec.data.load_ingredient_embeddings - INFO - Starting embedding retrieval process...
2025-09-14 13:49:25,505 - foodrec.data.load_ingredient_embeddings - INFO - ✓ Found existing embeddings file: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 13:49:25,505 - foodrec.data.load_ingredient_embeddings - INFO - Loading existing embeddings...


Like 0.4782608695652174
 Avoid 0.990990990990991
Cuisine 0.873015873015873
Overall0.7807559111906938
----------PATH_SEARCH_BIASE----------
####################Load Embeddings####################
Like 0.4772727272727273
 Avoid 1.0
Cuisine 0.8524590163934426
Overall0.7765772478887233


### Descriptive Data

### MEtriken wie bei Hypothese 1

In [7]:
paths = get_paths(ModelEnum.OpenAI.name)
pr_auc_raw = calc_metrics(query_set=query_set, paths=paths, model_name=ModelEnum.OpenAI, ref_include=False)

/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/OpenAI/no_biase/20_recommend__european_recipes_which_do_not_have_ingredient_fresh_lemon_juice?_OpenAI.jsonl
Recommend  european recipes which do not have ingredient fresh lemon juice?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/OpenAI/no_biase/42_what_are_latin_america_recipes_which_do_not_have_ingredient_chile_jelly?_OpenAI.jsonl
What are latin america recipes which do not have ingredient chile jelly?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/OpenAI/no_biase/46_what_are_european_dishes_which_don't_consist_of_eggplant?_OpenAI.jsonl
What are european dishes which don't consist of eggplant?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/convers

In [29]:
def calc_mean_rounds(df, paths, model_name: ModelEnum):
    def calc_median_rounds(df, model:ModelEnum, Path):
        ls = []
        for index, row in df.iterrows():
            persona_id = row["id"]
            query = row["query"]
            ls.append(calc_rounds(persona_id=persona_id, query=query, model=model, Path=Path))
        return np.mean(ls)
    print("Mean Rounds No Biase:", calc_median_rounds(df, model_name, paths['PATH_NO_BIASE']))
    print("Mean Rounds System Biase:", calc_median_rounds(df, model_name, paths['PATH_SYSTEM_BIASE']))
    print("Mean Search Biase:", calc_median_rounds(df, model_name, paths['PATH_SEARCH_BIASE']))
    print("Mean Both Biase:", calc_median_rounds(df, model_name, paths['PATH_BOTH']))

In [11]:
calc_mean_rounds(query_set, paths=paths, model_name=ModelEnum.OpenAI)

Mean Rounds No Biase: 1.44
Mean Rounds System Biase: 3.02
Mean Search Biase: 2.03
Mean Both Biase: 2.15


In [31]:
def calc_reward(query_set, paths, model_name: ModelEnum):
    reward_system_biase = get_reward_set(query_set, model_name, paths['PATH_SYSTEM_BIASE'])
    reward_system_no = get_reward_set(query_set, model_name, paths['PATH_NO_BIASE'])
    reward_search_biase = get_reward_set(query_set, model_name, paths['PATH_SEARCH_BIASE'])
    reward_both = get_reward_set(query_set, model_name, paths['PATH_BOTH'])
    print(f"Durchschnittlicher Score für System Biase: {reward_average_calculation(reward_system_biase)}")

    print(f"Durchschnittlicher Score fuer No Biase: {reward_average_calculation(reward_system_no)}")
    
    print(f"Durchschnittlicher Score für Search Biase: {reward_average_calculation(reward_search_biase)}")
    
    print(f"Durchschnittlicher Score für Both Biase: {reward_average_calculation(reward_both)}")
    


In [13]:
calc_reward(query_set=query_set, paths=paths, model_name=ModelEnum.OpenAI)

Durchschnittlicher Score für System Biase: Score: 0.6135 bei gamma=1, normalize=True
Durchschnittlicher Score fuer No Biase: Score: 0.3649 bei gamma=1, normalize=True
Durchschnittlicher Score für Search Biase: Score: 0.5266 bei gamma=1, normalize=True
Durchschnittlicher Score für Both Biase: Score: 0.5380 bei gamma=1, normalize=True


In [33]:
def calc_average_path_length(df, paths, model_name: ModelEnum):
    def calc_median_path_length(df, model:ModelEnum, Path):
        ls = []
        for index, row in df.iterrows():
            persona_id = row["id"]
            query = row["query"]
            ls.append(calc_path_length(persona_id=persona_id, query=query, model=model, Path=Path))
        return np.mean(ls)

    print("Mean Path Length No Biase:", calc_median_path_length(df, model_name, paths['PATH_NO_BIASE']))
    print("Mean Path Length Biase:", calc_median_path_length(df, model_name, paths['PATH_SYSTEM_BIASE']))
    print("Mean Path Search Biase:", calc_median_path_length(df, model_name, paths['PATH_SEARCH_BIASE']))
    print("Mean Path Both Biase:", calc_median_path_length(df, model_name, paths['PATH_BOTH']))

In [15]:
calc_average_path_length(df=query_set,paths=paths, model_name=ModelEnum.OpenAI)


Mean Path Length No Biase: 6.18
Mean Path Length Biase: 11.19
Mean Path Search Biase: 8.14
Mean Path Both Biase: 8.56


In [35]:
def calc_routing_accuracy(query_set, paths, model_name: ModelEnum):
    def routing_accuracy_calculation(reward_system):
        scores = []
        for i, episode in enumerate(reward_system, start=1):
            score = routing_accuracy(episode)
            scores.append(score)

        # Optional: Gesamtauswertung
        avg_score = np.mean(scores)
        return f"Score: {avg_score:.4f}"
    reward_system_biase = get_reward_set(query_set, model_name, paths['PATH_SYSTEM_BIASE'])
    reward_system_no = get_reward_set(query_set, model_name, paths['PATH_NO_BIASE'])
    reward_search_biase = get_reward_set(query_set, model_name, paths['PATH_SEARCH_BIASE'])
    reward_both = get_reward_set(query_set, model_name, paths['PATH_BOTH'])

    print(f"Durchschnittlicher Score für System Biase: {routing_accuracy_calculation(reward_system_biase)}")
    print(f"Durchschnittlicher Score fuer No Biase: {routing_accuracy_calculation(reward_system_no)}")
    print(f"Durchschnittlicher Score für Search Biase: {routing_accuracy_calculation(reward_search_biase)}")
    print(f"Durchschnittlicher Score fuer Both Biase: {routing_accuracy_calculation(reward_both)}")


In [17]:
calc_routing_accuracy(query_set=query_set,paths=paths, model_name=ModelEnum.OpenAI)

Durchschnittlicher Score für System Biase: Score: 0.8067
Durchschnittlicher Score fuer No Biase: Score: 0.6825
Durchschnittlicher Score für Search Biase: Score: 0.7633
Durchschnittlicher Score fuer Both Biase: Score: 0.7690


In [18]:
calc_mean_time(query_set, paths=paths, model_name=ModelEnum.OpenAI)

Mean Time No Biase: 279.17
Mean Time System Biase: 493.52
Mean Time Search Biase: 357.86
Mean Both Biase: 406.13


In [38]:
def get_last_reflector_answer(persona_id: int, query: str, model: ModelEnum, Path = None):
    query_stempt = query.replace(" ", "_").lower()
    id = f"{persona_id}_{query_stempt}_{model.name}"
    ls_search = []
    reflector = {}
    filepath = Path / f"{id}.jsonl"
    if not filepath.exists():
        return 0
    
    try:
        with open(filepath, "r", encoding="utf-8") as f:
            for line in f:
                
                line = line.strip()
                if not line:
                    continue
                try:
                    obj = json.loads(line)
                except json.JSONDecodeError:
                    continue  # kaputte Zeilen überspringen
                if obj.get("role") == "REFLECTOR":
                    reflector= obj
            meta = reflector["meta"]
            decision = meta['decision']
            if decision.lower() == "accept":
                return True
            else:
                return False
    except:
        return False

In [39]:
def calc_task_success_rate(query_set, paths, model:ModelEnum):
    def calc_individual_rate(query_set, Path, model:ModelEnum):
        ls = []
        for index, row in query_set.iterrows():
            persona_id = row["id"]
            query = row["query"]
            ls.append(get_last_reflector_answer(persona_id=persona_id, query=query, model=model, Path=Path))
        return np.mean(ls), ls     
    no_biase_mean, no_biase_raw =   calc_individual_rate(query_set= query_set, model=model, Path=paths['PATH_NO_BIASE'])
    system_biase, system_biase_raw = calc_individual_rate(query_set, model=model, Path=paths['PATH_SYSTEM_BIASE'])
    search_biase, search_biase_raw = calc_individual_rate(query_set=query_set, model=model, Path=paths['PATH_SEARCH_BIASE'])
    both_biase, search_both_biase = calc_individual_rate(query_set=query_set, model=model, Path=paths['PATH_BOTH'])
    print("Task Success Rate No Biase:", no_biase_mean)
    print("Task Success Rate Biase:", system_biase)
    print("Task Success Rate Search Biase:", search_biase)
    print("Task Success Rate Both Biase:", both_biase)
    return no_biase_raw, system_biase_raw, search_biase_raw, search_both_biase

In [ ]:
no_biase_raw, system_biase_raw, search_biase_raw, search_both_biase = calc_task_success_rate(query_set=query_set, paths=paths,model=ModelEnum.OpenAI)
eval_h2 = {
    "SystemBiase": system_biase_raw,
    "NoBiase":no_biase_raw,
    "SearchBiase":search_biase_raw,
    "BothBiase":search_both_biase
}

Task Success Rate No Biase: 0.85
Task Success Rate Biase: 0.6
Task Success Rate Search Biase: 0.84
Task Success Rate Both Biase: 0.83


In [41]:
def calc_keto(dict_biase: dict, df, keto_ratio_index: float = 0.8, mode: str = "top1") -> dict:
    """
    dict_biase: { query -> [ {recipe_dict}, ... ] } ODER { query -> {recipe_dict} }
    mode: 'top1' (nur erstes Rezept) oder 'any' (mind. ein Rezept ist ketogen)
    return: { query -> 0/1 }
    """
    def _is_keto(rec: dict) -> bool:
        obj = calc_keto_ratio(
            protein_g=rec.get("proteins", 0),
            fat_g=rec.get("fat", 0),
            carbs_g=rec.get("carbohydrates", 0),
        )
        if obj == np.inf:
            return 0
        return obj

    res = {}
    for _, row in df.iterrows():
        q = row["query"]

        # existiert der Query überhaupt?
        if q not in dict_biase:
            res[q] = 0
            continue

        items = dict_biase[q]

        # Normalisieren auf Liste von Rezepten
        if items is None:
            res[q] = 0
            continue
        if isinstance(items, dict):
            items = [items]
        if not isinstance(items, (list, tuple)) or len(items) == 0:
            res[q] = 0
            continue

        # Modus: top1 oder any
        if mode == "top1":
            res[q] = float(_is_keto(items[0]))
        elif mode == "any":
            res[q] = float(any(_is_keto(r) for r in items))
        else:
            raise ValueError("mode must be 'top1' or 'any'")

    return res


In [23]:
dict_search_engine, dict_search_engine_search = get_search_engine(paths['PATH_SEARCH_ENGINE'])
dict_system_biase,  dict_system_biase_search, ref_system_biase  = get_dicts_set(df=query_set, model=ModelEnum.OpenAI, Path=paths['PATH_SYSTEM_BIASE'])
dict_no_biase,      dict_no_biase_search, ref_no_biase      = get_dicts_set(df=query_set, model=ModelEnum.OpenAI, Path=paths['PATH_NO_BIASE'])
dict_search_biase,  dict_search_biase_search, ref_search_biase  = get_dicts_set(query_set, ModelEnum.OpenAI, paths['PATH_SEARCH_BIASE'])
dict_both,          dict_both_search, ref_both_biase          = get_dicts_set(query_set, ModelEnum.OpenAI, paths['PATH_BOTH'])

/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/OpenAI/no_biase/20_recommend__european_recipes_which_do_not_have_ingredient_fresh_lemon_juice?_OpenAI.jsonl
Recommend  european recipes which do not have ingredient fresh lemon juice?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/OpenAI/no_biase/42_what_are_latin_america_recipes_which_do_not_have_ingredient_chile_jelly?_OpenAI.jsonl
What are latin america recipes which do not have ingredient chile jelly?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/OpenAI/no_biase/46_what_are_european_dishes_which_don't_consist_of_eggplant?_OpenAI.jsonl
What are european dishes which don't consist of eggplant?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/convers

In [24]:
eval = {
    "SystemBiase": calc_keto(df=query_set, dict_biase=dict_system_biase),
    "NoBiase":calc_keto(df=query_set, dict_biase=dict_no_biase),
    "SearchEngine": calc_keto(df=query_set, dict_biase=dict_search_engine),
    "SearchBiase":calc_keto(df=query_set, dict_biase=dict_search_biase),
    "BothBiase":calc_keto(df=query_set, dict_biase=dict_both)
}

In [25]:
import pandas as pd

df_wide = pd.DataFrame(eval)              
df_wide = df_wide.reset_index()            
df_wide = df_wide.rename(columns={"index": "query"})

In [26]:
for col in df_wide.columns:
    if col == "query": 
        continue
    x = df_wide[col].dropna().to_numpy()
    print(f"{col} Mean: {np.median(x)}")


SystemBiase Mean: 1.010412667903395
NoBiase Mean: 0.21465310605669502
SearchEngine Mean: 0.2503780723728942
SearchBiase Mean: 0.9819557717116554
BothBiase Mean: 1.1648577159671825


In [27]:
def calc_open_ai_costs(df, paths, model_name: ModelEnum):
    def calc_costs(df, model:ModelEnum, Path):
        ls_costs = []
        ls_input_token = []
        ls_output_token = []

        for index, row in df.iterrows():
            persona_id = row["id"]
            query = row["query"]
            try:
                input_token, output_token, costs = calc_openai_costs(persona_id=persona_id, query=query, model=model, Path=Path)
                ls_costs.append(costs)
                ls_input_token.append(input_token)
                ls_output_token.append(output_token)
            except: 
                print(query)
                continue
        return ls_input_token, ls_output_token, ls_costs
    
    ls_input_token_no, ls_output_token_no, ls_costs_no = calc_costs(df, model_name, paths['PATH_NO_BIASE'])
    ls_input_token_system, ls_output_token_system, ls_costs_system = calc_costs(df, model_name, paths['PATH_SYSTEM_BIASE'])
    ls_input_token_search, ls_output_token_search, ls_costs_search = calc_costs(df, model_name, paths['PATH_SEARCH_BIASE'])
    ls_input_token_both, ls_output_token_both, ls_costs_both = calc_costs(df, model_name, paths['PATH_BOTH'])

    total_costs = sum(ls_costs_no) + sum(ls_costs_system) + sum(ls_costs_search) + sum(ls_costs_both)
    print(len(ls_costs_no))
    print(f'Total Costs: ${total_costs}')
    print(f"Costs No Biase: ${np.mean(ls_costs_no)} ")
    print(f"Costs System Biase: ${np.mean(ls_costs_system)}")
    print(f"Costs Search Biase: ${np.mean(ls_costs_search)}")
    print(f"Costs Both Biase: ${np.mean(ls_costs_both)}")

In [28]:
calc_open_ai_costs(df=query_set,paths=paths, model_name=ModelEnum.OpenAI)

Recommend  european recipes which do not have ingredient fresh lemon juice?
What are latin america recipes which do not have ingredient chile jelly?
What are european dishes which don't consist of eggplant?
What are european recipes that do not consist of ingredient sherry vinaigrette?
What are middle east or whitefish recipes which do not have ingredient crappies?
What are asia dishes which don't consist of butter - flavored cooking spray?
What are short-grain-rice, european or north_american dishes that do not have ingredient powdered ginger?
What middle east dishes can I make without chicken bouillon cubes?
92
Total Costs: $19.744441750000004
Costs No Biase: $0.03743325 
Costs System Biase: $0.06465689499999999
Costs Search Biase: $0.045768772500000006
Costs Both Biase: $0.052580160000000015


## Comparison with Gemini Pro

In [26]:
recommendation_accuracy(query_set, ModelEnum.GEMINIPRO)

2025-09-14 14:05:21,638 - foodrec.data.load_ingredient_embeddings - INFO - EmbeddingLoader initialized with path: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 14:05:21,639 - foodrec.data.load_ingredient_embeddings - INFO - Starting embedding retrieval process...
2025-09-14 14:05:21,639 - foodrec.data.load_ingredient_embeddings - INFO - ✓ Found existing embeddings file: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 14:05:21,640 - foodrec.data.load_ingredient_embeddings - INFO - Loading existing embeddings...


----------PATH_NO_BIASE----------
####################Load Embeddings####################


2025-09-14 14:05:23,347 - foodrec.data.load_ingredient_embeddings - INFO - EmbeddingLoader initialized with path: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 14:05:23,348 - foodrec.data.load_ingredient_embeddings - INFO - Starting embedding retrieval process...
2025-09-14 14:05:23,348 - foodrec.data.load_ingredient_embeddings - INFO - ✓ Found existing embeddings file: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 14:05:23,348 - foodrec.data.load_ingredient_embeddings - INFO - Loading existing embeddings...


Like 0.5833333333333334
 Avoid 0.9814814814814815
Cuisine 0.8333333333333334
Overall0.7993827160493828
----------PATH_SYSTEM_BIASE----------
####################Load Embeddings####################


2025-09-14 14:05:25,002 - foodrec.data.load_ingredient_embeddings - INFO - EmbeddingLoader initialized with path: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 14:05:25,003 - foodrec.data.load_ingredient_embeddings - INFO - Starting embedding retrieval process...
2025-09-14 14:05:25,003 - foodrec.data.load_ingredient_embeddings - INFO - ✓ Found existing embeddings file: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 14:05:25,003 - foodrec.data.load_ingredient_embeddings - INFO - Loading existing embeddings...


Like 0.5365853658536586
 Avoid 0.9900990099009901
Cuisine 0.8392857142857143
Overall0.7886566966801211
----------PATH_BOTH----------
####################Load Embeddings####################


2025-09-14 14:05:26,744 - foodrec.data.load_ingredient_embeddings - INFO - EmbeddingLoader initialized with path: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 14:05:26,744 - foodrec.data.load_ingredient_embeddings - INFO - Starting embedding retrieval process...
2025-09-14 14:05:26,744 - foodrec.data.load_ingredient_embeddings - INFO - ✓ Found existing embeddings file: /Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/ingredient_embeddings/ingredient_embeddings_ALL_RECIPE.csv
2025-09-14 14:05:26,745 - foodrec.data.load_ingredient_embeddings - INFO - Loading existing embeddings...


Like 0.5384615384615384
 Avoid 0.9897959183673469
Cuisine 0.9655172413793104
Overall0.8312582327360653
----------PATH_SEARCH_BIASE----------
####################Load Embeddings####################
Like 0.5897435897435898
 Avoid 0.98989898989899
Cuisine 0.8771929824561403
Overall0.81894518736624


In [27]:
paths = get_paths(ModelEnum.GEMINIPRO.name)
pr_auc_raw = calc_metrics(query_set=query_set, paths=paths, model_name=ModelEnum.GEMINIPRO, ref_include=False)

/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/GEMINIPRO/no_biase/20_recommend__european_recipes_which_do_not_have_ingredient_fresh_lemon_juice?_GEMINIPRO.jsonl
Recommend  european recipes which do not have ingredient fresh lemon juice?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/GEMINIPRO/no_biase/46_what_are_european_dishes_which_don't_consist_of_eggplant?_GEMINIPRO.jsonl
What are european dishes which don't consist of eggplant?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/GEMINIPRO/no_biase/47_what_are_european_recipes_that_do_not_consist_of_ingredient_sherry_vinaigrette?_GEMINIPRO.jsonl
What are european recipes that do not consist of ingredient sherry vinaigrette?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/syste

In [30]:
calc_mean_rounds(query_set, paths=paths, model_name=ModelEnum.GEMINIPRO)

Mean Rounds No Biase: 2.08
Mean Rounds System Biase: 4.25
Mean Search Biase: 2.62
Mean Both Biase: 3.89


In [32]:
calc_reward(query_set=query_set, paths=paths, model_name=ModelEnum.GEMINIPRO)

Durchschnittlicher Score für System Biase: Score: 0.7323 bei gamma=1, normalize=True
Durchschnittlicher Score fuer No Biase: Score: 0.4599 bei gamma=1, normalize=True
Durchschnittlicher Score für Search Biase: Score: 0.5976 bei gamma=1, normalize=True
Durchschnittlicher Score für Both Biase: Score: 0.7048 bei gamma=1, normalize=True


In [34]:
calc_average_path_length(df=query_set,paths=paths, model_name=ModelEnum.GEMINIPRO)


Mean Path Length No Biase: 8.14
Mean Path Length Biase: 14.75
Mean Path Search Biase: 9.87
Mean Path Both Biase: 13.69


In [36]:
calc_routing_accuracy(query_set=query_set,paths=paths, model_name=ModelEnum.GEMINIPRO)

Durchschnittlicher Score für System Biase: Score: 0.8662
Durchschnittlicher Score fuer No Biase: Score: 0.7299
Durchschnittlicher Score für Search Biase: Score: 0.7988
Durchschnittlicher Score fuer Both Biase: Score: 0.8524


In [37]:
calc_mean_time(query_set, paths=paths, model_name=ModelEnum.GEMINIPRO)

Mean Time No Biase: 266.14
Mean Time System Biase: 905.95
Mean Time Search Biase: 395.26
Mean Both Biase: 721.99


In [40]:
no_biase_raw, system_biase_raw, search_biase_raw, search_both_biase = calc_task_success_rate(query_set=query_set, paths=paths,model=ModelEnum.GEMINIPRO)
eval_h2 = {
    "SystemBiase": system_biase_raw,
    "NoBiase":no_biase_raw,
    "SearchBiase":search_biase_raw,
    "BothBiase":search_both_biase
}

Task Success Rate No Biase: 0.8
Task Success Rate Biase: 0.33
Task Success Rate Search Biase: 0.78
Task Success Rate Both Biase: 0.43


In [42]:
dict_search_engine, dict_search_engine_search = get_search_engine(paths['PATH_SEARCH_ENGINE'])
dict_system_biase,  dict_system_biase_search, ref_system_biase  = get_dicts_set(df=query_set, model=ModelEnum.GEMINIPRO, Path=paths['PATH_SYSTEM_BIASE'])
dict_no_biase,      dict_no_biase_search, ref_no_biase      = get_dicts_set(df=query_set, model=ModelEnum.GEMINIPRO, Path=paths['PATH_NO_BIASE'])
dict_search_biase,  dict_search_biase_search, ref_search_biase  = get_dicts_set(query_set, ModelEnum.GEMINIPRO, paths['PATH_SEARCH_BIASE'])
dict_both,          dict_both_search, ref_both_biase          = get_dicts_set(query_set, ModelEnum.GEMINIPRO, paths['PATH_BOTH'])

/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/GEMINIPRO/no_biase/20_recommend__european_recipes_which_do_not_have_ingredient_fresh_lemon_juice?_GEMINIPRO.jsonl
Recommend  european recipes which do not have ingredient fresh lemon juice?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/GEMINIPRO/no_biase/46_what_are_european_dishes_which_don't_consist_of_eggplant?_GEMINIPRO.jsonl
What are european dishes which don't consist of eggplant?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/system/foodrec/config/dataset/conversation/GEMINIPRO/no_biase/47_what_are_european_recipes_that_do_not_consist_of_ingredient_sherry_vinaigrette?_GEMINIPRO.jsonl
What are european recipes that do not consist of ingredient sherry vinaigrette?
not enough values to unpack (expected 3, got 2)
/Users/noah/Documents/github/MultiAgentBiase/syste

In [43]:
eval = {
    "SystemBiase": calc_keto(df=query_set, dict_biase=dict_system_biase),
    "NoBiase":calc_keto(df=query_set, dict_biase=dict_no_biase),
    "SearchEngine": calc_keto(df=query_set, dict_biase=dict_search_engine),
    "SearchBiase":calc_keto(df=query_set, dict_biase=dict_search_biase),
    "BothBiase":calc_keto(df=query_set, dict_biase=dict_both)
}

In [44]:
df_wide = pd.DataFrame(eval)              
df_wide = df_wide.reset_index()            
df_wide = df_wide.rename(columns={"index": "query"})

In [45]:
for col in df_wide.columns:
    if col == "query": 
        continue
    x = df_wide[col].dropna().to_numpy()
    print(f"{col} Mean: {np.median(x)}")

SystemBiase Mean: 1.0010899274947511
NoBiase Mean: 0.24492656474119026
SearchEngine Mean: 0.2503780723728942
SearchBiase Mean: 0.972796922504326
BothBiase Mean: 1.0539998428126967


## COSTS

In [47]:
def calc_open_gemini_costs(df, paths, model_name: ModelEnum):
    def calc_costs(df, model:ModelEnum, Path):
        ls_costs = []
        ls_input_token = []
        ls_output_token = []

        for index, row in df.iterrows():
            persona_id = row["id"]
            query = row["query"]
            try:
                input_token, output_token, costs = calc_gemini_costs(persona_id=persona_id, query=query, model=model, Path=Path)
                ls_costs.append(costs)
                ls_input_token.append(input_token)
                ls_output_token.append(output_token)
            except Exception as e: 
                print(e)
                continue
        return ls_input_token, ls_output_token, ls_costs
    
    ls_input_token_no, ls_output_token_no, ls_costs_no = calc_costs(df, model_name, paths['PATH_NO_BIASE'])
    ls_input_token_system, ls_output_token_system, ls_costs_system = calc_costs(df, model_name, paths['PATH_SYSTEM_BIASE'])
    ls_input_token_search, ls_output_token_search, ls_costs_search = calc_costs(df, model_name, paths['PATH_SEARCH_BIASE'])
    ls_input_token_both, ls_output_token_both, ls_costs_both = calc_costs(df, model_name, paths['PATH_BOTH'])
    total_costs = sum(ls_costs_no) + sum(ls_costs_system) + sum(ls_costs_search) + sum(ls_costs_both)
    print(f'Total Costs: ${total_costs}')
    print(f"Costs No Biase: ${np.mean(ls_costs_no)} ")
    print(f"Costs System Biase: ${np.mean(ls_costs_system)}")
    print(f"Costs Search Biase: ${np.mean(ls_costs_search)}")
    print(f"Costs Both Biase: ${np.mean(ls_costs_both)}")

In [6]:
calc_open_gemini_costs(df=query_set,paths=get_paths(ModelEnum.Gemini.name), model_name=ModelEnum.Gemini)

2025-09-12 14:23:29,879 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:23:29,985 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:23:30,071 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:23:30,223 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:23:30,307 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:23:30,393 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:23:30,47

cannot unpack non-iterable int object


2025-09-12 14:24:48,172 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:24:48,275 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:24:48,352 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:24:48,451 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:24:48,532 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:24:48,609 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:24:48,69

cannot unpack non-iterable int object


2025-09-12 14:26:28,947 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:26:29,074 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:26:29,160 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:26:29,247 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:26:29,333 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:26:29,412 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:26:29,49

...

cannot unpack non-iterable int object


2025-09-12 14:50:51,095 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:50:51,197 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:50:51,280 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:50:51,396 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:50:51,486 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:50:51,577 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:50:51,71

cannot unpack non-iterable int object


2025-09-12 14:54:42,608 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:54:42,681 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:54:42,756 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:54:42,829 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:54:42,913 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:54:43,000 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 14:54:43,08

[104, 32, 32, 50, 32, 32, 32, 32, 100, 32, 68, 32, 32, 32, 50, 68, 32, 50, 32, 32, 32, 32, 32, 32, 32, 32, 50, 32, 32, 68, 32, 32, 32, 32, 32, 56, 32, 50, 50, 32, 100, 86, 32, 50, 50, 50, 32, 32, 32, 100, 32, 100, 32, 32, 32, 68, 32, 32, 86, 68, 32, 32, 32, 32, 32, 32, 32, 32, 100, 32, 50, 32, 32, 50, 32, 100, 32, 68, 68, 32, 32, 32, 32, 32, 68, 32, 100, 32, 100, 68, 32, 32, 50, 50, 32, 56]
0.18677280000000004
Total Costs: $0.18677280000000004
Costs No Biase: $0.0003971687500000001 
Costs System Biase: $0.000572583157894737
Costs Search Biase: $0.00042558541666666674
Costs Both Biase: $0.0005561770833333334


In [6]:
calc_open_gemini_costs(df=query_set.iloc[:2],paths=get_paths(ModelEnum.Gemini.name), model_name=ModelEnum.Gemini)

2025-09-12 15:05:53,748 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 15:05:53,859 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 15:05:53,965 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 15:05:54,085 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 15:05:54,182 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 15:05:54,279 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.0-flash:countTokens "HTTP/1.1 200 OK"
2025-09-12 15:05:54,36

[104, 32]
0.002556600000000001
Total Costs: $0.002556600000000001
Costs No Biase: $0.0004108000000000001 
Costs System Biase: $0.0002842000000000001
Costs Search Biase: $0.00028610000000000007
Costs Both Biase: $0.00029720000000000007


In [48]:
calc_open_gemini_costs(df=query_set,paths=get_paths(ModelEnum.GEMINIPRO.name), model_name=ModelEnum.GEMINIPRO)

2025-09-14 14:10:54,972 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:10:55,070 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:10:55,176 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:10:55,286 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:10:55,459 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:10:55,565 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:10:55,682 - httpx - 

cannot unpack non-iterable int object


2025-09-14 14:13:06,967 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:13:07,048 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:13:07,131 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:13:07,211 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:13:07,357 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:13:07,441 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:13:07,518 - httpx - 

cannot unpack non-iterable int object
cannot unpack non-iterable int object


2025-09-14 14:15:17,938 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:15:18,018 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:15:18,097 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:15:18,175 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:15:18,259 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:15:18,336 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:15:18,414 - httpx - 

...

cannot unpack non-iterable int object


2025-09-14 14:19:09,593 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:19:09,706 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:19:09,789 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:19:09,878 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:19:09,973 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:19:10,080 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:19:10,163 - httpx - 

cannot unpack non-iterable NoneType object


2025-09-14 14:53:03,716 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:53:03,807 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:53:03,918 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:53:04,017 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:53:04,175 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:53:04,269 - httpx - INFO - HTTP Request: POST https://generativelanguage.googleapis.com/v1beta/models/gemini-2.5-pro:countTokens "HTTP/1.1 200 OK"
2025-09-14 14:53:04,425 - httpx - 

Total Costs: $8.629959999999999
Costs No Biase: $0.0154981914893617 
Costs System Biase: $0.028645224999999993
Costs Search Biase: $0.01679292929292929
Costs Both Biase: $0.026461074999999997
